## Import Library

In [38]:
# from humpback import *

import pandas as pd
import numpy as np
from datetime import datetime
import ta

from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler

from keras.models import Sequential
from keras.layers import LSTM, Dense, Dropout

from backtesting import Backtest, Strategy

## Defining Functions

Functions in this section would be moved to humpback.py after testing for tidiness

In [46]:
import os
import pandas as pd
import numpy as np
import ta
from dotenv import load_dotenv
from binance.client import Client
from sklearn.preprocessing import MinMaxScaler

def connectBinanceAPI():
    load_dotenv()
    API_KEY    = os.getenv('API_KEY')
    API_SECRET = os.getenv('API_SECRET')

    return Client(API_KEY, API_SECRET)

def getBinanceData(client,
                   symbol: str,
                   interval: str,
                   start_str: str,
                   end_str: str):
    kline = client.get_historical_klines(symbol=symbol,
                                         interval=interval,
                                         start_str=start_str,
                                         end_str=end_str)
    columns = ['index',
               'Open',
               'High',
               'Low',
               'Close',
               'Volume']
    data = pd.DataFrame(kline).iloc[:,:6]
    data.columns  = columns
    data['index'] = pd.to_datetime(data['index'], unit='ms')
    data.set_index('index', inplace=True)
    data = data.astype(float)
    data.dropna(inplace=True)
    
    return data

def create_previous_data_data(data, num_points):
    data_lists = []

    for i in range(len(data)):
        if i < num_points:
            continue
        
        prev_data = [data.iloc[i-n, 0] if i >= n else None for n in range(1, num_points+1)]
        data_lists.append(prev_data)

    columns = [f"X_{n}" for n in range(1, num_points+1)]
    prev_data = pd.DataFrame(data_lists, columns=columns)

    return prev_data

def sma(data, window=14):
    sma = ta.trend.SMAIndicator(pd.Series(data.Close), window=window).sma_indicator()
    return sma

def ema(data, window=14):
    ema = ta.trend.EMAIndicator(pd.Series(data.Close), window=window).ema_indicator()
    return ema

def rsi(data, window=14):
    rsi = ta.momentum.RSIIndicator(pd.Series(data.Close), window=window).rsi()
    return rsi

def macd(data):
    macd = ta.trend.MACD(pd.Series(data.Close)).macd()
    return macd

def atr(data):
    return ta.volatility.AverageTrueRange(data.High, data.Low, data.Close).average_true_range()

def signal_h(data):
    return ta.volatility.BollingerBands(pd.Series(data)).bollinger_hband()
def signal_l(data):
    return ta.volatility.BollingerBands(pd.Series(data)).bollinger_lband()

def transformData(data):
    scaler = MinMaxScaler(feature_range=(0,1))
    scaled_data = scaler.fit_transform(data)
    scaled_data = pd.DataFrame(scaled_data)
    columns = ['Close']
    scaled_data.columns = columns

    return scaler, scaled_data

def addSMA(data, sma_start: int, sma_end: int, sma_step: int):
    sma_range = range(sma_start, sma_end, sma_step)

    for window in sma_range:
        # SMA/Close
        # relative value of SMA to closing price
        data[f'SMA_{window}'] = sma(data, window) / data['Close']

    for i in range(len(sma_range)):
        for j in range(i+1, len(sma_range)):
            # (SMA_1 - SMA_2) / Close
            data[f'SMA_DELTA_{sma_range[i]}_{sma_range[j]}'] = data[f'SMA_{sma_range[i]}'] - data[f'SMA_{sma_range[j]}']

    return data

def addEMA(data, ema_start: int, ema_end: int, ema_step: int):
    ema_range = range(ema_start, ema_end, ema_step)

    for window in ema_range:
        # EMA/Close
        # relative value of EMA to closing price
        data[f'EMA_{window}'] = ema(data, window) / data['Close']

    for i in range(len(ema_range)):
        for j in range(i+1, len(ema_range)):
            # (EMA_1 - EMA_2) / Close
            data[f'EMA_DELTA_{ema_range[i]}_{ema_range[j]}'] = data[f'EMA_{ema_range[i]}'] - data[f'EMA_{ema_range[j]}']

    return data

def featureGeneration(data, sma_start: int = 20,
                            sma_end  : int = 100,
                            sma_step : int = 20,
                            ema_start: int = 20,
                            ema_end  : int = 100,
                            ema_step : int = 20):
    """
    Input
    --------
    X: pd.DataFrame


    Output
    --------
    X: pd.DataFrame
    """
    close = data.Close

    # SMA
    data = addSMA(data=data, sma_start=sma_start, sma_end=sma_end, sma_step=sma_step)

    # EMA
    data = addEMA(data=data, ema_start=ema_start, ema_end=ema_end, ema_step=ema_step)

    # RSI
    data['RSI'] = rsi(data=data)

    # MACD
    data['MACD'] = macd(data=data)

    # ATR
    data['ATR'] = atr(data=data)

    # BollingerBands
    upper = signal_h(data.Close)
    lower = signal_l(data.Close)

    data['BB_upper'] = (upper - close) / close
    data['BB_lower'] = (lower - close) / close
    data['BB_width'] = (upper - lower) / close

    # Garman Klass Volatility
    data['garman_klass_vol'] = ((np.log(data['High'])-np.log(data['Low']))**2)/2-(2*np.log(2)-1)*((np.log(data['Close'])-np.log(data['Open']))**2)

    # Output    
    data = data.dropna().astype(float)
    return data

def getReturn(data, y_column: str = 'Close', dropna: bool = True):
    """Reads OHLCV and compute the period return based on closing price

    Args:
        data (pd.DataFrame): Raw OHLCV
        y_column (str)     : which column the return is calculated based on

    Returns:
        data (pd.DataFrame): with one more column, and dropped na
    """

    data['Return'] = data[y_column].shift(-1) / data[y_column] - 1
    if dropna:
        data.dropna(inplace=True)
    return data

def getXy(data, y_column: str = 'Return'):
    """split data into feature and target

    Args:
        data (pd.DataFrame): dataframe
        y_column (str, optional): target column name. Defaults to 'Return'.

    Returns:
        X: feature
        y: target
    """
    data.dropna(inplace=True)
    y = data[[y_column]]
    X = data.drop(y_column, axis=1)
    return X, y



## Defining Model

In [40]:
class MyModel:
    def __init__(self):
        self.optimizer = 'adam'
        self.loss      = 'mean_squared_error'

    def trainModel(self, data_X, data_y, epochs: int = 20, batch_size: int = 32):
        self.model = Sequential()
        self.model.add(LSTM(units=50,
                            return_sequences=True,
                            input_shape=(data_X.shape[1],1)))
        self.model.add(Dropout(0.2))

        self.model.add(LSTM(units=50,
                            return_sequences=True))
        self.model.add(Dropout(0.2))

        self.model.add(LSTM(units=50,
                            return_sequences=True))
        self.model.add(Dropout(0.2))

        self.model.add(LSTM(units=50))
        self.model.add(Dropout(0.2))

        self.model.add(Dense(units=1))

        self.model.compile(optimizer=self.optimizer,
                           loss=self.loss)

        self.model.fit(data_X, data_y,
                       epochs=epochs,
                       batch_size=batch_size)
    
    def preprocessData(self, data):
        """
        Transform the data using min max scaler
        Initialise and fit a scaler using training data
        """
        self.scaler = MinMaxScaler(feature_range=(0,1))
        scaled_data = scaler.fit_transform(data)
        return scaled_data

    def predictModel(self, data_X):
        return self.model.predict(data_X)
    
    def get_model(self):
        return self.model

## Defining Strategy

In [60]:
class MyStr(Strategy):
    # Variables:
    train_size = 0.7
    buy_threshold  = .01
    sell_threshold = .01


    def init(self):
        # Declare indicators you will use in the strategy:
        self.getData()
        self.model_init()

        # Plot y for inspection
        # _, y = getXy(getReturn(self.data.df, y_column='Close', dropna=False), 'Return')
        # self.I(np.array, y, name='y_true')

        # Prepare empty, all-NaN forecast indicator
        self.forecasts = self.I(lambda: np.repeat(np.nan, len(self.data)), name='forecast')

    def next(self):
        if len(self.data) < len(self.y_train):
            return

        X = featureGeneration(self.data.df.iloc[-120:])
        forecast = self.model.predictModel(X.iloc[-1])[0]

        # Update the plotted "forecast" indicator
        self.forecasts[-1] = forecast
        
        if forecast > self.buy_threshold and not self.position.is_long:
            tp = self.data.Close[-1] + 2 * X['ATR'][-1]
            sl = self.data.Close[-1] - 2 * X['ATR'][-1]
            self.buy(size=.2, tp=tp, sl=sl)

        if forecast < self.sell_threshold and not self.position.is_short:
            tp = self.data.Close[-1] - 2 * X['ATR'][-1]
            sl = self.data.Close[-1] + 2 * X['ATR'][-1]
            self.sell(size=.2, tp=tp, sl=sl)

########################################

    def getData(self):
        data_train, data_test = train_test_split(self.data.df,
                                                 train_size=self.train_size,
                                                 shuffle=False)
        data_train, data_test = [getReturn(data, 'Close') for data in [data_train, data_test]]
        data_train, data_test = [featureGeneration(data)  for data in [data_train, data_test]]
        self.X_train, self.y_train = getXy(data_train, 'Return')
        self.X_test , self.y_test  = getXy(data_test , 'Return')

    def model_init(self):
        self.model = MyModel()
        self.model.trainModel(self.X_train, self.y_train, epochs=1)

    def get_model(self):
        return self.model.get_model()


## Parameters

This section contains all the parameters.

In [42]:
# This chunk specifies the data

symbol = 'BTCUSDT'
interval = '1h'
window_LSTM = 60

start_str = int(datetime(2020,1,1,0,0).timestamp() * 1000)
end_str    = int(datetime(2023,12,31,0,0).timestamp() * 1000)

In [43]:
# This chunk specifies the model



## Obtain data

This section outputs training and testing data for the use of the following sections.

In [44]:
client = connectBinanceAPI()

In [8]:
data_raw = getBinanceData(client=client,
                          symbol=symbol,
                          interval=interval,
                          start_str=start_str,
                          end_str=end_str)

## Backtesting

In [61]:
bt    = Backtest(data_raw, MyStr, cash = 1000000, commission=0.00075)
stats = bt.run()

/Users/taryn.tsui/Documents/Alvin/GitHub/alvinlui99/Algo Trading/.venv/lib/python3.12/site-packages/keras/src/layers/rnn/rnn.py:204: UserWarning: Do not pass an `input_shape`/`input_dim` argument to a layer. When using Sequential models, prefer using an `Input(shape)` object as the first layer in the model instead.
  super().__init__(**kwargs)


764/764 ━━━━━━━━━━━━━━━━━━━━ 34s 37ms/step - loss: 2.2798e-04
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 520ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step


/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:36: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  tp = self.data.Close[-1] - 2 * X['ATR'][-1]
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:37: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 20ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 21ms/step


/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = f

...

/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast


1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 82ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 19ms/step


/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = f

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 49ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 22ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 23ms/step


/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/3728121736.py:28: DeprecationWarning: Conversion of an array with ndim > 0 to a scalar is deprecated, and will error in future. Ensure you extract a single element from your array before performing this operation. (Deprecated NumPy 1.25.)
  self.forecasts[-1] = forecast
/var/folders/ft/h3fjv72s4jdftdb2szbgyggr0000gp/T/ipykernel_14694/2637361661.py:94: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/in

## Results

In [63]:
bt.plot()

/Users/taryn.tsui/Documents/Alvin/GitHub/alvinlui99/Algo Trading/.venv/lib/python3.12/site-packages/backtesting/_plotting.py:122: UserWarning: Data contains too many candlesticks to plot; downsampling to '4H'. See `Backtest.plot(resample=...)`
  warnings.warn(f"Data contains too many candlesticks to plot; downsampling to {freq!r}. "
/Users/taryn.tsui/Documents/Alvin/GitHub/alvinlui99/Algo Trading/.venv/lib/python3.12/site-packages/backtesting/_plotting.py:126: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  df = df.resample(freq, label='right').agg(OHLCV_AGG).dropna()
/Users/taryn.tsui/Documents/Alvin/GitHub/alvinlui99/Algo Trading/.venv/lib/python3.12/site-packages/backtesting/_plotting.py:128: FutureWarning: 'H' is deprecated and will be removed in a future version, please use 'h' instead.
  indicators = [_Indicator(i.df.resample(freq, label='right').mean()
/Users/taryn.tsui/Documents/Alvin/GitHub/alvinlui99/Algo Trading/.venv/lib/p

TypeError: Index.get_loc() got an unexpected keyword argument 'method'

In [64]:
stats.tail()

Expectancy [%]                                            -0.145116
SQN                                                       -2.578598
_strategy                                                     MyStr
_equity_curve                                  Equity  DrawdownP...
_trades                Size  EntryBar  ExitBar    EntryPrice    ...
dtype: object

In [65]:
stats['_equity_curve']

Equity  DrawdownPct  DrawdownDuration
index                                                             
2019-12-31 16:00:00  1000000.000000     0.000000               NaT
2019-12-31 17:00:00  1000000.000000     0.000000               NaT
2019-12-31 18:00:00  1000000.000000     0.000000               NaT
2019-12-31 19:00:00  1000000.000000     0.000000               NaT
2019-12-31 20:00:00  1000000.000000     0.000000               NaT
...                             ...          ...               ...
2023-12-30 12:00:00   810307.169442     0.231463               NaT
2023-12-30 13:00:00   810190.019442     0.231574               NaT
2023-12-30 14:00:00   809545.709442     0.232185               NaT
2023-12-30 15:00:00   809153.189442     0.232557               NaT
2023-12-30 16:00:00   808717.309802     0.232971 411 days 11:00:00

[35009 rows x 3 columns]